In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import os
import sys
from pathlib import Path

workding_dir = str(Path.cwd().parent)
os.chdir(workding_dir)
sys.path.append(workding_dir)
print("workding dir:", workding_dir)

workding dir: /home/inflaton/code/projects/courses/llm-finetuning


In [3]:
from dotenv import find_dotenv, load_dotenv

found_dotenv = find_dotenv(".env")

if len(found_dotenv) == 0:
    found_dotenv = find_dotenv(".env.example")
print(f"loading env vars from: {found_dotenv}")
load_dotenv(found_dotenv, override=True)

loading env vars from: /home/inflaton/code/projects/courses/llm-finetuning/.env


True

In [4]:
import os

model_name = os.getenv("MODEL_NAME")
token = os.getenv("HF_TOKEN") or None
load_in_4bit = os.getenv("LOAD_IN_4BIT") == "true"
local_model = os.getenv("LOCAL_MODEL")
hub_model = os.getenv("HUB_MODEL")
num_train_epochs = int(os.getenv("NUM_TRAIN_EPOCHS") or 0)
data_path = os.getenv("DATA_PATH")
results_path = os.getenv("RESULTS_PATH")

max_seq_length = 2048  # Choose any! We auto support RoPE Scaling internally!
dtype = (
    None  # None for auto detection. Float16 for Tesla T4, V100, Bfloat16 for Ampere+
)

model_name, load_in_4bit, local_model, hub_model, max_seq_length, num_train_epochs, dtype, data_path, results_path

('unsloth/Qwen2-0.5B-Instruct',
 True,
 None,
 None,
 2048,
 6,
 None,
 'datasets/mac/mac.tsv',
 'results/mac-results_lf-r2.csv')

In [5]:
!nvidia-smi

Fri Jul  5 20:43:31 2024       
+---------------------------------------------------------------------------------------+
| NVIDIA-SMI 545.23.07              Driver Version: 546.12       CUDA Version: 12.3     |
|-----------------------------------------+----------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |         Memory-Usage | GPU-Util  Compute M. |
|                                         |                      |               MIG M. |
|=========================================+======================+======================|
|   0  NVIDIA GeForce RTX 4080 ...    On  | 00000000:01:00.0 Off |                  N/A |
| N/A   53C    P8               3W / 150W |      0MiB / 12282MiB |      0%      Default |
|                                         |                      |                  N/A |
+-----------------------------------------+----------------------+--

In [6]:
%%time
!python --version
!pip show flash-attn

Python 3.11.9
CPU times: user 9.63 ms, sys: 584 μs, total: 10.2 ms
Wall time: 561 ms


In [7]:
def evaluate_model_all_epochs(model_name, num_train_epochs, adapter_path_base, load_in_4bit=True):
    os.environ["MODEL_NAME"] = model_name 
    os.environ["LOAD_IN_4BIT"] = "true" if load_in_4bit else "false"
    for i in range(num_train_epochs + 1):
        print(f"Epoch {i}")
        if i == 0:
            os.unsetenv("ADAPTER_NAME_OR_PATH")
        else:
            adapter_path = f"{adapter_path_base}/checkpoint-{560 * i}"
            os.environ["ADAPTER_NAME_OR_PATH"] = adapter_path
            
        !python llm_toolkit/eval_lf.py

In [8]:
%%time

evaluate_model_all_epochs("Qwen/Qwen2-0.5B-Instruct", num_train_epochs, "llama-factory/saves/qwen2-0.5b-bf16/lora/sft", load_in_4bit=False)

Epoch 0
loading env vars from: /home/inflaton/code/projects/courses/llm-finetuning/.env
Adding /home/inflaton/code/projects/courses/llm-finetuning to sys.path
loading /home/inflaton/code/projects/courses/llm-finetuning/llm_toolkit/translation_utils.py
[nltk_data] Downloading package wordnet to /home/inflaton/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package punkt to /home/inflaton/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package omw-1.4 to /home/inflaton/nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!
Qwen/Qwen2-0.5B-Instruct None False datasets/mac/mac.tsv results/mac-results_lf-r2.csv
(1) GPU = NVIDIA GeForce RTX 4080 Laptop GPU. Max memory = 11.994 GB.
0.0 GB of memory reserved.
loading model: Qwen/Qwen2-0.5B-Instruct
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.
(2) GPU = NVIDIA GeForce RTX 4080 Lapt

In [ ]:
%%time

evaluate_model_all_epochs("unsloth/qwen2-0.5b-instruct-bnb-4bit" , num_train_epochs, "llama-factory/saves/qwen2-0.5b/lora/sft")

In [9]:
%%time

evaluate_model_all_epochs("Qwen/Qwen2-1.5B-Instruct", num_train_epochs, "llama-factory/saves/qwen2-1.5b-bf16/lora/sft", load_in_4bit=False)

Epoch 0
loading env vars from: /home/inflaton/code/projects/courses/llm-finetuning/.env
Adding /home/inflaton/code/projects/courses/llm-finetuning to sys.path
loading /home/inflaton/code/projects/courses/llm-finetuning/llm_toolkit/translation_utils.py
[nltk_data] Downloading package wordnet to /home/inflaton/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package punkt to /home/inflaton/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package omw-1.4 to /home/inflaton/nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!
Qwen/Qwen2-1.5B-Instruct None False datasets/mac/mac.tsv results/mac-results_lf-r2.csv
(1) GPU = NVIDIA GeForce RTX 4080 Laptop GPU. Max memory = 11.994 GB.
0.0 GB of memory reserved.
loading model: Qwen/Qwen2-1.5B-Instruct
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.
(2) GPU = NVIDIA GeForce RTX 4080 Lapt

In [ ]:
%%time

evaluate_model_all_epochs("unsloth/qwen2-1.5b-instruct-bnb-4bit" , num_train_epochs, "llama-factory/saves/qwen2-1.5b/lora/sft")